In [123]:
import matplotlib
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import string
from nltk.corpus import stopwords
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfVectorizer

In [124]:
data = pd.read_csv("중복값제거.csv")

In [125]:
#data1 = data[data['keyword'] == '성공 마인드'].index
#data = data.drop(data1)

data

Unnamed: 0                                            content keyword  \
0               0                       라코레 자개공예 와인오프너 특별한 집들이선물로 딱!      공예   
1               1                               [삼청동] 서울공예박물관 & 조선김밥      공예   
2               2                   이색취미 비즈공예:코바늘뜨기로 시드비즈 목걸이만들기(도안)      공예   
3               3                          종이공예 눈꽃송이 눈결정체 만들기(도안 포함)      공예   
4               4                               취미생활추천 지점토 공예 화분 만들기      공예   
...           ...                                                ...     ...   
23476       27603  #오늘의뉴스 2021년 1월 14일 1. 코로나 ‘집콕’에 ‘확찐’ 아이들 → 가톨...   아동 교육   
23477       27605  이렇게 많이 글을 쓰게 될줄 몰랐네요. 많은 분들이 쪽지주셔서 어딘지 물어보시고, ...   아동 교육   
23478       27607  어느날, 별거없는 초등학생 고아 몇 명 앞에 책임감이 투철한 교사가 무릎꿇고 빌게 ...   아동 교육   
23479       27608  #오늘의뉴스 2020년 9월7일 1. 당정청, 7조원대 4차 추경 합의 → 전 국민...   아동 교육   
23480       27609  생각의 흐름대로 편하게 적기 위해 간단체로 쓰니 양해바랍니다. -----------...   아동 교육   

       site  
0       네이버  
1       네이버  
2       네이버  
3       네이버  
4       네이버  
...     ...  
23476  블라인드  
23477  블라인드  
23478  블라인드  
23479  블라인드  
23480  블라인드  

[23481 rows x 4 columns]

In [126]:
# 키워드 기준으로 소팅
data_sorted = data.sort_values('keyword')
data_sorted

Unnamed: 0                                            content keyword  \
18127       21324  같은 개발자면 좋나요? 밥 카페 영화관 이런 루트 말고 그냥 같은 직종이면 좀더 이...      개발   
18156       21370              생각도 못한 아이템이다 http://naver.me/F5uXFktB      개발   
18155       21369  안녕하세요 선배님들, 입사를 앞둔 신입 개발자입니다. 이런 질문이 요즘 하도 올라와...      개발   
18154       21368  동생이 개발자 직군으로 취업 예정인데, 스타트업이나 작은 회사의 경우 초봉이 어느정...      개발   
18153       21364  나는 우선 영상전공이고 지금 7-8년차인데 너무 거지같고 번아웃이 와서 직종을 바꾸...      개발   
...           ...                                                ...     ...   
1520         1569   텍스트 위젯 플러그인 만들기 커스텀 포스트 플러그인 만들기 소스코드 수정 방법 워...      창업   
1521         1570     메모지 / 체크리스트 색감을 이용한 굿즈 달력 도무송 스티커 패키지 노트패드 ...      창업   
1522         1571     아이디어스 입점하기 경쟁사 자료조사하고 상품 기획하기      저도 고민을 참...      창업   
1511         1559      1만 달러로 몇 시간 만에 95,900원을 벌었습니다. 당연한 이야기지만, ...      창업   
1552         1601       반갑습니다. 미쳐야미친다 광성&아키우노TV 박대표입니다. 온라인상에 디벨로...      창업   

         site  
18127    블라인드  
18156    블라인드  
18155    블라인드  
18154    블라인드  
18153    블라인드  
...       ...  
1520   클래스101  
1521   클래스101  
1522   클래스101  
1511   클래스101  
1552   클래스101  

[23481 rows x 4 columns]

In [144]:
data_sorted.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 23481 entries, 18127 to 1552
Data columns (total 4 columns):
 #   Column      Non-Null Count  Dtype 
---  ------      --------------  ----- 
 0   Unnamed: 0  23481 non-null  int64 
 1   content     23481 non-null  object
 2   keyword     23481 non-null  object
 3   site        23481 non-null  object
dtypes: int64(1), object(3)
memory usage: 917.2+ KB


In [145]:
#키워드(카테고리)만 list화

keyword = list(set(data_sorted['keyword']))
len(keyword)

22

In [174]:
keyword

['금융',
 '언어',
 '부업',
 '재테크',
 '베이킹',
 '직무교육',
 '개발',
 '음악',
 '데이터',
 '외국어',
 '음료',
 '디자인',
 '창업',
 '사진',
 '요리',
 '영상',
 '공예',
 '성공 마인드',
 '아동 교육',
 '글쓰기',
 '운동',
 '드로잉']

In [146]:
#conents(내용)에 해당하는 부분만 'docs'라는 리스트로 만듦

docs = list(data_sorted['content'])

In [147]:
docs

['같은 개발자면 좋나요? 밥 카페 영화관 이런 루트 말고 그냥 같은 직종이면 좀더 이해하고 잘통할거같은데 사내커플은 하기싫고 궁금하당..🥺',
 '생각도 못한 아이템이다 http://naver.me/F5uXFktB',
 '안녕하세요 선배님들, 입사를 앞둔 신입 개발자입니다. 이런 질문이 요즘 하도 올라와 지겨우실 텐데 또 vs질 해서 죄송합니다ㅠㅠ 처음이자 마지막으로 질문 드립니다. 이번에 네이버와 쿠팡 공채에 합격하게 되어 행복한 고민을 하고 있습니다. 희망직군은 BE입니다. 둘다 공채라 최종 배치가 어떻게 될지도 변수이네요. 연봉은 다들 아시는대로 쿠팡이 더 많고, 집에서 거리는 정자가 20분 잠실이 1시간이상이라 일장일단이 있어 어디로 가야할지 정말 고민됩니다. 읽어주셔서 감사하겠습니다! 다들 행복하세용',
 '동생이 개발자 직군으로 취업 예정인데, 스타트업이나 작은 회사의 경우 초봉이 어느정도일까요? 회사에서 생각하는 초봉을 먼저 말하라고 했다는데 전혀 감이 없네요ㅠㅠ 계약 연봉하고, 성과급(?)같은 거 포함하는 영끌 연봉 나눠서 알려주시면 감사하겠습니다',
 '나는 우선 영상전공이고 지금 7-8년차인데 너무 거지같고 번아웃이 와서 직종을 바꾸려고해 이바닥 이제 너무 치가 떨리고 ptsd오거든 그래서 그동안 계속 눈여겨본 개발직군에 도전해보고 싶은 맘이 있는데 전망도 있어보이고 (개인적으로 조용히 혼자 일하는게 편한 타입이야) 목표는 딥러닝 머신러닝도 할 수있는 개발자이지만 한번에 도달하기는 어려워 보이니 일단 웹개발자로 시작해서 익숙해지면 점점 넓혀볼려고.. 일단 국비로 배워볼생각 하고있어 현 개발직군 형아드라 비전공자가 하기엔 많이 힘들까?? 현실적인 조언좀 부탁해 ㅠㅠ 무작정',
 'ㅠㅠㅠ 소개팅으로 판교근무하는 개발자 남친 생겻는데 ㅠㅠ 오빤데도 아니 ㅠㅠㅠㅠㅠㅠㅠ 순수하기도 하고 왜케 귀여워 미치것냠 ㅠㅠㅠㅠㅠㅠ (나도 직업 개발자야!!) 개발자인데 댕댕이여서 가끔 오글멘트 날리는데 ㅠㅠㅠ 그래그래 참아줄수있어 ㅠㅠㅠㅠㅠ 난 개발자 추천이야'

# 데이터 전처리

In [148]:
import re
import requests
from bs4 import BeautifulSoup


from konlpy.tag import Okt 
okt = Okt()

In [149]:
# http로 시작되는 url제거
remove_url = [re.sub(r"http[s]?://(?:[a-zA-Z]|[0-9]|[$-_@.&+]|[!*\(\),]|(?:%[0-9a-fA-F][0-9a-fA-F]))+", " ", str(content)) for content in docs]

# 숫자 제거
remove_num = [re.sub(r'\d+',' ', str(content)) for content in remove_url]

# 영어 제거 
remove_alpha = [re.sub('[a-zA-Z]' , ' ', str(content)) for content in remove_num]

# Hashtag 제거
remove_tag = [re.sub('[#]+[0-9a-zA-Z_]+', ' ', str(content)) for content in remove_alpha]

# 특수문자 제거
remove_special = [re.sub('[^0-9a-zA-Zㄱ-ㅎ가-힣]', ' ', str(content)) for content in remove_tag]

#정규식(Regular Expression)이용해서 정규화
lawdata = [re.sub(r"[^가-힣A-Za-z0-9]", " ", str(content)) for content in remove_special]


   # 쓰레기 단어 제거
   #text = re.sub('[&]+[a-z]+', ' ', text)

   # 특정 문자 제거
   #for i in ['!','@','#','*'] :
       #new_id = new_id.replace(i, "")

   # 띄어쓰기 제거
   #text = text.replace('\n',' ')

In [150]:
lawdata[:20]

['같은 개발자면 좋나요  밥 카페 영화관 이런 루트 말고 그냥 같은 직종이면 좀더 이해하고 잘통할거같은데 사내커플은 하기싫고 궁금하당   ',
 '생각도 못한 아이템이다  ',
 '안녕하세요 선배님들  입사를 앞둔 신입 개발자입니다  이런 질문이 요즘 하도 올라와 지겨우실 텐데 또   질 해서 죄송합니다   처음이자 마지막으로 질문 드립니다  이번에 네이버와 쿠팡 공채에 합격하게 되어 행복한 고민을 하고 있습니다  희망직군은   입니다  둘다 공채라 최종 배치가 어떻게 될지도 변수이네요  연봉은 다들 아시는대로 쿠팡이 더 많고  집에서 거리는 정자가  분 잠실이  시간이상이라 일장일단이 있어 어디로 가야할지 정말 고민됩니다  읽어주셔서 감사하겠습니다  다들 행복하세용',
 '동생이 개발자 직군으로 취업 예정인데  스타트업이나 작은 회사의 경우 초봉이 어느정도일까요  회사에서 생각하는 초봉을 먼저 말하라고 했다는데 전혀 감이 없네요   계약 연봉하고  성과급   같은 거 포함하는 영끌 연봉 나눠서 알려주시면 감사하겠습니다',
 '나는 우선 영상전공이고 지금    년차인데 너무 거지같고 번아웃이 와서 직종을 바꾸려고해 이바닥 이제 너무 치가 떨리고     오거든 그래서 그동안 계속 눈여겨본 개발직군에 도전해보고 싶은 맘이 있는데 전망도 있어보이고  개인적으로 조용히 혼자 일하는게 편한 타입이야  목표는 딥러닝 머신러닝도 할 수있는 개발자이지만 한번에 도달하기는 어려워 보이니 일단 웹개발자로 시작해서 익숙해지면 점점 넓혀볼려고   일단 국비로 배워볼생각 하고있어 현 개발직군 형아드라 비전공자가 하기엔 많이 힘들까   현실적인 조언좀 부탁해    무작정',
 '    소개팅으로 판교근무하는 개발자 남친 생겻는데    오빤데도 아니         순수하기도 하고 왜케 귀여워 미치것냠         나도 직업 개발자야    개발자인데 댕댕이여서 가끔 오글멘트 날리는데     그래그래 참아줄수있어       난 개발자 추천이야',
 '안녕하세요 이직한지 얼마 안되었는데 

# 형태소 분석

## tokenized

In [151]:
#morphs는 형태소 단위로 구문을 분석(형태소 단위로 토크나이즈)

lawdata_tokened_morphs = []

for doc in lawdata:
    newdoc = okt.morphs(doc)
    lawdata_tokened_morphs.append(newdoc)

In [152]:
lawdata_tokened_morphs[:2]

[['같은',
  '개발자',
  '면',
  '좋나요',
  '밥',
  '카페',
  '영화관',
  '이런',
  '루트',
  '말고',
  '그냥',
  '같은',
  '직종',
  '이',
  '면',
  '좀더',
  '이해',
  '하고',
  '잘',
  '통',
  '할거',
  '같은데',
  '사',
  '내',
  '커플',
  '은',
  '하기',
  '싫고',
  '궁금하당'],
 ['생각', '도', '못', '한', '아이템', '이다']]

## stopwords

In [153]:
## stopwords 파일 불러오기
## open('파일경로.txt', 'rt', encoding='UTF8')
file_path = "/Users/parkjuhyeon/datamining/textmining/stopwords-ko.txt"


with open(file_path, 'rt', encoding='UTF8') as f:
    lines = f.read().splitlines()

stop_list = lines

In [154]:
stop_list

['아',
 '휴',
 '아이구',
 '아이쿠',
 '아이고',
 '어',
 '나',
 '우리',
 '저희',
 '따라',
 '의해',
 '을',
 '를',
 '에',
 '의',
 '가',
 '으로',
 '로',
 '에게',
 '뿐이다',
 '의거하여',
 '근거하여',
 '입각하여',
 '기준으로',
 '예하면',
 '예를 들면',
 '예를 들자면',
 '저',
 '소인',
 '소생',
 '저희',
 '지말고',
 '하지마',
 '하지마라',
 '다른',
 '물론',
 '또한',
 '그리고',
 '비길수 없다',
 '해서는 안된다',
 '뿐만 아니라',
 '만이 아니다',
 '만은 아니다',
 '막론하고',
 '관계없이',
 '그치지 않다',
 '그러나',
 '그런데',
 '하지만',
 '든간에',
 '논하지 않다',
 '따지지 않다',
 '설사',
 '비록',
 '더라도',
 '아니면',
 '만 못하다',
 '하는 편이 낫다',
 '불문하고',
 '향하여',
 '향해서',
 '향하다',
 '쪽으로',
 '틈타',
 '이용하여',
 '타다',
 '오르다',
 '제외하고',
 '이 외에',
 '이 밖에',
 '하여야',
 '비로소',
 '한다면 몰라도',
 '외에도',
 '이곳',
 '여기',
 '부터',
 '기점으로',
 '따라서',
 '할 생각이다',
 '하려고하다',
 '이리하여',
 '그리하여',
 '그렇게 함으로써',
 '하지만',
 '일때',
 '할때',
 '앞에서',
 '중에서',
 '보는데서',
 '으로써',
 '로써',
 '까지',
 '해야한다',
 '일것이다',
 '반드시',
 '할줄알다',
 '할수있다',
 '할수있어',
 '임에 틀림없다',
 '한다면',
 '등',
 '등등',
 '제',
 '겨우',
 '단지',
 '다만',
 '할뿐',
 '딩동',
 '댕그',
 '대해서',
 '대하여',
 '대하면',
 '훨씬',
 '얼마나',
 '얼마만큼',
 '얼마큼',
 '남짓',
 '여',
 '얼마간',
 '약간',
 '다소',
 '좀',
 '조

In [155]:
#한국어 불용어 사전 불러와서 불용어 제거

result = [] 
for w in lawdata_tokened_morphs: 
    if w not in stop_list: 
        result.append(w) 

print(result)

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [156]:
result

[['같은',
  '개발자',
  '면',
  '좋나요',
  '밥',
  '카페',
  '영화관',
  '이런',
  '루트',
  '말고',
  '그냥',
  '같은',
  '직종',
  '이',
  '면',
  '좀더',
  '이해',
  '하고',
  '잘',
  '통',
  '할거',
  '같은데',
  '사',
  '내',
  '커플',
  '은',
  '하기',
  '싫고',
  '궁금하당'],
 ['생각', '도', '못', '한', '아이템', '이다'],
 ['안녕하세요',
  '선배',
  '님',
  '들',
  '입사',
  '를',
  '앞둔',
  '신입',
  '개발자',
  '입니다',
  '이런',
  '질문',
  '이',
  '요즘',
  '하도',
  '올라와',
  '지겨우실',
  '텐데',
  '또',
  '질',
  '해서',
  '죄송합니다',
  '처음',
  '이자',
  '마지막',
  '으로',
  '질문',
  '드립니다',
  '이번',
  '에',
  '네이버',
  '와',
  '쿠팡',
  '공채',
  '에',
  '합격',
  '하게',
  '되어',
  '행복한',
  '고민',
  '을',
  '하고',
  '있습니다',
  '희망',
  '직',
  '군',
  '은',
  '입니다',
  '둘다',
  '공채',
  '라',
  '최종',
  '배치',
  '가',
  '어떻게',
  '될지도',
  '변수',
  '이네',
  '요',
  '연봉',
  '은',
  '다',
  '들',
  '아시는대로',
  '쿠팡',
  '이',
  '더',
  '많고',
  '집',
  '에서',
  '거리',
  '는',
  '정자',
  '가',
  '분',
  '잠실',
  '이',
  '시',
  '간이',
  '상',
  '이라',
  '일장일단',
  '이',
  '있어',
  '어디',
  '로',
  '가야',
  '할지',
  '정말',
  '고민',
  '됩니다',
  '읽어주셔서

In [157]:
#리스트 안에 담긴 값(단어모음 형태)들을 각각 문장화

rawdata = []

for doc in result:
    doc2 = ' '.join(doc)
    rawdata.append(doc2)

In [158]:
rawdata

['같은 개발자 면 좋나요 밥 카페 영화관 이런 루트 말고 그냥 같은 직종 이 면 좀더 이해 하고 잘 통 할거 같은데 사 내 커플 은 하기 싫고 궁금하당',
 '생각 도 못 한 아이템 이다',
 '안녕하세요 선배 님 들 입사 를 앞둔 신입 개발자 입니다 이런 질문 이 요즘 하도 올라와 지겨우실 텐데 또 질 해서 죄송합니다 처음 이자 마지막 으로 질문 드립니다 이번 에 네이버 와 쿠팡 공채 에 합격 하게 되어 행복한 고민 을 하고 있습니다 희망 직 군 은 입니다 둘다 공채 라 최종 배치 가 어떻게 될지도 변수 이네 요 연봉 은 다 들 아시는대로 쿠팡 이 더 많고 집 에서 거리 는 정자 가 분 잠실 이 시 간이 상 이라 일장일단 이 있어 어디 로 가야 할지 정말 고민 됩니다 읽어주셔서 감사하겠습니다 다 들 행복하세용',
 '동생 이 개발자 직 군 으로 취업 예정 인데 스타트업 이나 작은 회사 의 경우 초봉 이 어느 정도 일까 요 회사 에서 생각 하는 초봉 을 먼저 말 하 라고 했다는데 전혀 감 이 없네요 계약 연봉 하고 성과급 같은 거 포함 하는 영 끌 연봉 나눠서 알려주시면 감사하겠습니다',
 '나 는 우선 영상 전공 이고 지금 년차 인데 너무 거지같고 번 아웃 이 와서 직종 을 바꾸려고해 이 바닥 이제 너무 치가 떨리고 오거 든 그래서 그동안 계속 눈 여겨 본 개발 직 군 에 도전 해보고 싶은 맘 이 있는데 전망 도 있어 보이 고 개인 적 으로 조용히 혼자 일 하는게 편한 타입 이야 목표 는 딥 러닝 머신 러닝 도 할 수 있는 개발자 이지만 한번 에 도달 하기는 어려워 보이니 일단 웹개발자 로 시작 해서 익숙해지면 점점 넓혀 볼려고 일단 국비 로 배워 볼 생각 하고있어 현 개발 직 군 형 아드라 비 전공자 가 하기엔 많이 힘들까 현실 적 인 조언 좀 부탁 해 무작정',
 '소개팅 으로 판교 근무 하 는 개발자 남친 생겻는데 오 빤데도 아니 순수하기도 하고 왜케 귀여워 미치것 냠 나도 직업 개발자 야 개발자 인데 댕댕 이 여서 가끔 오 글 멘트 날리는데 그래그래

## 명사 추출 함수 정의

In [159]:
#명사만 추출하는 함수 정의(토크나이즈해서 명사만 추출)

import string
def noun_process(text):
    nouns = okt.nouns(text)
    #nouns = [word for word in nouns if len(word) > 1]
    return nouns

In [160]:
print(rawdata[0])
print(noun_process(rawdata[0]))

같은 개발자 면 좋나요 밥 카페 영화관 이런 루트 말고 그냥 같은 직종 이 면 좀더 이해 하고 잘 통 할거 같은데 사 내 커플 은 하기 싫고 궁금하당
['개발자', '면', '밥', '카페', '영화관', '루트', '그냥', '직종', '이', '면', '좀더', '이해', '통', '사', '내', '커플', '은']


## TF-IDF

In [161]:
## 미리 만들어준 명사추출함수(noun_process)를 사용하여, 전체내용(rawdata/문장형태 list) -> 명사만추출 -> 다시문장화(list) 전처리
# 즉, 문장에서 명사만 추출해서 명사로만 이루어진 문장으로 만들어줌

docs_list = [' '.join(noun_process(s)) for s in lawdata]

In [162]:
## 전처리한 데이터 확인 (명사만 추출되어 문장화 된 형태)
docs_list[:5] 

['개발자 밥 카페 영화관 루트 그냥 직종 좀더 이해 통 커플',
 '생각 못 아이템',
 '선배 입사 신입 개발자 질문 요즘 또 질 처음 이자 마지막 질문 이번 네이버 쿠팡 공채 합격 고민 희망 직 공채 최종 배치 변수 요 연봉 쿠팡 더 집 거리 정자 분 잠실 간이 일장일단 어디 가야 정말 고민',
 '동생 개발자 직 취업 예정 스타트업 회사 경우 초봉 정도 요 회사 생각 초봉 먼저 말 전혀 감 계약 연봉 성과급 거 포함 끌 연봉',
 '나 우선 영상 전공 지금 년차 번 아웃 직종 바닥 이제 치가 오거 그동안 계속 눈 개발 직 도전 맘 전망 보이 개인 혼자 일 타입 목표 딥 러닝 머신 러닝 수 개발자 한번 도달 일단 웹개발자 시작 점점 일단 국비 볼 생각 현 개발 직 형 아드라 비 전공자 현실 조언 좀 부탁 무작정']

In [163]:
from sklearn.feature_extraction.text import TfidfVectorizer

# 2개 미만의 문서(min_df) 또는 90%이상(max_df)에 나타나는 용어는 제외합니다.

# min-df는 DF(document-frequency)의 최소 빈도값을 설정해주는 파라미터  (DF는 특정 단어가 나타나는 '문서의 수')
# 최소 min-dr가 2로 설정되었으니, 특정 단어가 나타나는 문서가 1개밖에 안되는 것들은 모두 탈락


vec = TfidfVectorizer(max_df=0.90, min_df=2 )

In [164]:
features = vec.fit_transform(docs_list)

# NMF 모델 생성

In [165]:
type(features)

scipy.sparse.csr.csr_matrix

In [166]:
print(features)

  (0, 15723)	0.36029122405935454
  (0, 12512)	0.19289145113163955
  (0, 14044)	0.3717636639876359
  (0, 14604)	0.37438449781881494
  (0, 1566)	0.21140069298735825
  (0, 4306)	0.37905843906074205
  (0, 11059)	0.48979074188357
  (0, 15597)	0.24342437351460025
  (0, 398)	0.25900810451228984
  (1, 9948)	0.8848983142588516
  (1, 7930)	0.4657842563052583
  (2, 13691)	0.10565762346309536
  (2, 92)	0.17124675296681433
  (2, 10425)	0.11692249440760154
  (2, 209)	0.24623053190813493
  (2, 13123)	0.23741807136758014
  (2, 13756)	0.2634527243149828
  (2, 489)	0.15436201217603487
  (2, 10908)	0.13596994369633275
  (2, 6460)	0.18985522480137168
  (2, 6156)	0.15582477372823353
  (2, 15305)	0.160097653767616
  (2, 18818)	0.1687744906993927
  (2, 852)	0.20562963284256391
  (2, 17964)	0.17256853045515033
  :	:
  (23480, 3186)	0.0355959909720119
  (23480, 13806)	0.04273765252697526
  (23480, 16524)	0.03188980300284208
  (23480, 10767)	0.031211086329984556
  (23480, 3883)	0.03973301586257216
  (23480, 754

In [167]:
from sklearn.decomposition import NMF

#n_topics = 카테고리수

nmf = NMF(n_components=22)
nmf.fit(features)

NMF(n_components=22)

In [168]:
# 활성화된 상위 단어를 표시하는 기능
# n_top_words=? (?: 상위 몇개의 단어를 표시할지 결정)

def display_top_words(n_top_words, feature_names, nmf):
    for i, topic_vec in enumerate(nmf.components_):
        print(i, end=' ')
    for fid in topic_vec.argsort()[-1:-n_top_words-1:-1]:
        print(feature_names[fid], end=' ')
    print()


In [169]:
display_top_words(50, vec.get_feature_names(), nmf)

0 1 2 3 4 5 6 7 8 9 10 11 12 13 14 15 16 17 18 19 20 21 디자인 디자이너 캐릭터 브랜드 작업 제작 포토샵 레터 케이크 기획 패턴 로고 생각 활용 제품 그래픽 포스터 이모티콘 글자 실무 이미지 비누 완성 이번 가방 하나 과정 주얼리 시각 직접 일러스트레이터 일러스트 전공 기본 포트폴리오 만들기 패션 가요 문구 한글 컨셉 모델링 파일 방법 기법 패키지 판매 스타일 폰트 카드 


In [170]:
##### 각 주제에 대해 활성화된 상위 단어를 표시하는 기능

def topic_table(n_top_words, feature_names, nmf):
    topics = {}
    for i, topic_vec in enumerate(nmf.components_):
        topic_descr = ''
        for fid in topic_vec.argsort()[-1:-n_top_words-1:-1]:
            topic_descr = topic_descr + feature_names[fid] + " "
        topics[i] = topic_descr
    return pd.DataFrame({'Top_Topic_Terms': topics})


# 각 카테고리별로 가장많이 등장한 상위 단어 15개(15terms)
topic_df = topic_table(15, vec.get_feature_names(), nmf)


In [171]:
topic_df

Top_Topic_Terms
0   그림 캐릭터 표현 일러스트 그리기 그릴 방법 인물 채색 완성 클래스 느낌 생각 여러...
1     클래스 모든 방법 세상 여러분 강의 시작 영상 통해 사용 작품 시간 활용 과정 가지 
2   운동 근육 오늘 여자 필라테스 헬스장 식단 다이어트 헬스 하체 시간 루틴 근력 어깨...
3       부업 월급 회사 주말 정도 본업 요즘 만원 시간 수익 퇴근 용돈 혹시 알바 직장 
4    공부 재테크 시작 자격증 그냥 진짜 스터디 시간 요즘 혼자 관련 생각 학원 관심 주말 
5      추천 부탁 노래 혹시 영상 요즘 재테크 메뉴 해주 공유 학원 취미 보고 멜론 한번 
6   사진 카메라 보정 남자 여행 촬영 취미 그냥 소개팅 친구 영상 생각 핸드폰 오늘 인스타 
7    주식 투자 부동산 재테크 적금 수익 코인 정도 자산 만원 펀드 현금 경제 아파트 시작 
8   요리 남자 취미 레시피 음식 만들기 재료 샐러드 자취 해먹 여행 메뉴 파스타 여자 진짜 
9     개발 회사 개발자 연봉 정도 직무 이직 업무 교육 경력 면접 지원 신입 분위기 혹시 
10  데이터 분석 파이썬 빅데이터 러닝 무제한 금제 머신 사이언스 업무 통계 마케팅 직무...
11  드로잉 디지털 학원 아이패드 프로 크리 에이트 그리기 일러스트 미술 색연필 취미 타...
12    사람 글쓰기 모임 진짜 그냥 생각 영상 친구 혹시 주변 쪽지 지금 보고 얘기 유튜브 
13  음악 노래 신문 교육 피아노 클래식 공유 연주 장르 재즈 작곡 악기 요즘 피아니스트...
14  창업 생각 사업 카페 아이템 회사 아이디어 시작 매출 비용 스타트업 마케팅 관심 판...
15  언어 파이썬 프로그래밍 사용 자바 코딩 개념 교환 문제 선택 프로그램 다른 모듈 만...
16     금융 대출 은행 신용 금리 지금 공기업 기업 보험 지주 하나 정도 배당 증권 연봉 
17  베이 케이크 만들기 쿠키 디저트 스콘 레시피 비건 재료 오븐 마들렌 반죽 초코 파운...
18  영어 중국어 아이 일본어 회화 단어 한국어 발음 문장 학습 엄마 스페인어 정도 표현...
19   음료 오늘 스벅 쿠폰 커피 카페 진짜 미션 무료 라떼 스타벅스 아아 그냥 텀블러 교환 
20  외국어 자격증 토익 일본어 하나 시험 해외 학원 능력 취미 영업 중국어 필수 그냥 ...
21  디자인 디자이너 캐릭터 브랜드 작업 제작 포토샵 레터 케이크 기획 패턴 로고 생각 ...

In [180]:
# Manually label topics
# 위에 데이터에 맞게 label topics 임의분류 (위에 표의 순서에 맞게, 묶여진 클러스터별로 topic 이름을 부여해줌)

topic_df['Label'] =['공예', '성공 마인드', '운동', '부업', '직무교육', '영상', '사진', '재테크', '요리', '개발', '데이터', '드로잉', '글쓰기', '음악', '창업', '언어', '금융', '베이킹', '아동 교육', '음료', '외국어','디자인']

In [181]:
topic_df

Top_Topic_Terms   Label
0   그림 캐릭터 표현 일러스트 그리기 그릴 방법 인물 채색 완성 클래스 느낌 생각 여러...      공예
1     클래스 모든 방법 세상 여러분 강의 시작 영상 통해 사용 작품 시간 활용 과정 가지   성공 마인드
2   운동 근육 오늘 여자 필라테스 헬스장 식단 다이어트 헬스 하체 시간 루틴 근력 어깨...      운동
3       부업 월급 회사 주말 정도 본업 요즘 만원 시간 수익 퇴근 용돈 혹시 알바 직장       부업
4    공부 재테크 시작 자격증 그냥 진짜 스터디 시간 요즘 혼자 관련 생각 학원 관심 주말     직무교육
5      추천 부탁 노래 혹시 영상 요즘 재테크 메뉴 해주 공유 학원 취미 보고 멜론 한번       영상
6   사진 카메라 보정 남자 여행 촬영 취미 그냥 소개팅 친구 영상 생각 핸드폰 오늘 인스타       사진
7    주식 투자 부동산 재테크 적금 수익 코인 정도 자산 만원 펀드 현금 경제 아파트 시작      재테크
8   요리 남자 취미 레시피 음식 만들기 재료 샐러드 자취 해먹 여행 메뉴 파스타 여자 진짜       요리
9     개발 회사 개발자 연봉 정도 직무 이직 업무 교육 경력 면접 지원 신입 분위기 혹시       개발
10  데이터 분석 파이썬 빅데이터 러닝 무제한 금제 머신 사이언스 업무 통계 마케팅 직무...     데이터
11  드로잉 디지털 학원 아이패드 프로 크리 에이트 그리기 일러스트 미술 색연필 취미 타...     드로잉
12    사람 글쓰기 모임 진짜 그냥 생각 영상 친구 혹시 주변 쪽지 지금 보고 얘기 유튜브      글쓰기
13  음악 노래 신문 교육 피아노 클래식 공유 연주 장르 재즈 작곡 악기 요즘 피아니스트...      음악
14  창업 생각 사업 카페 아이템 회사 아이디어 시작 매출 비용 스타트업 마케팅 관심 판...      창업
15  언어 파이썬 프로그래밍 사용 자바 코딩 개념 교환 문제 선택 프로그램 다른 모듈 만...      언어
16     금융 대출 은행 신용 금리 지금 공기업 기업 보험 지주 하나 정도 배당 증권 연봉       금융
17  베이 케이크 만들기 쿠키 디저트 스콘 레시피 비건 재료 오븐 마들렌 반죽 초코 파운...     베이킹
18  영어 중국어 아이 일본어 회화 단어 한국어 발음 문장 학습 엄마 스페인어 정도 표현...   아동 교육
19   음료 오늘 스벅 쿠폰 커피 카페 진짜 미션 무료 라떼 스타벅스 아아 그냥 텀블러 교환       음료
20  외국어 자격증 토익 일본어 하나 시험 해외 학원 능력 취미 영업 중국어 필수 그냥 ...     외국어
21  디자인 디자이너 캐릭터 브랜드 작업 제작 포토샵 레터 케이크 기획 패턴 로고 생각 ...     디자인

In [182]:
#'다이어트 메뉴 샐러드 파스타 레시피' 이라는 글을 모델에 넣었을때, 8번째(요리) 카테고리가 출력되는 것 확인
new_review = ['다이어트 메뉴 샐러드 파스타 레시피']
nmf.transform(vec.transform(new_review)).argsort(axis=1)[:,-1]

array([8])

In [183]:
#0번째(공예) 카테고리가 출력되는 것 확인
new_review = ['오늘 그림 색깔 핑크 패턴 스티커']
nmf.transform(vec.transform(new_review)).argsort(axis=1)[:,-1]

array([0])

In [188]:
#7번째(재테크) 카테고리가 출력되는 것 확인
new_review = ['삼성전자 은행 돈 주식 실망 이직 자격증 술']
nmf.transform(vec.transform(new_review)).argsort(axis=1)[:,-1]

array([7])

# 클러스터링한 데이터가 얼마나 잘 묶여졌는지 정확도 확인(참고)

In [189]:
#(문서,단어) 형태이다.

print(features.shape)

(23481, 18852)


In [190]:
type(features)

scipy.sparse.csr.csr_matrix

In [191]:
# term-document matrix가 필요하다.
# 현재의 Matrix를 transposed matrix(전치행렬)로 바꿔줘야 함.
# compressed sparse(희소행렬: 행렬의 값이 대부분 0일때) row matrix인 docs를 transpose 한다. (행열바꾸기 -> (단어, 글) 형태의 matrix로)

features_trans = features.transpose()
type(features_trans) 

print('Shape of Sparse Matrix: ', features_trans.shape)
print('Amount of Non-Zero occurrences: ', features_trans.nnz)

Shape of Sparse Matrix:  (18852, 23481)
Amount of Non-Zero occurrences:  772709


In [192]:
nmf = NMF(n_components=22)
nmf.fit(features_trans)

NMF(n_components=22)

In [193]:
H = nmf.components_

In [194]:
#shpae 형식 = (클러스터개수, document 개수)
H.shape

(22, 23481)

In [196]:
# 전체 글에 대해서 어떤 index(클러스터)가 best인지 출력

pred_labels = H.argmax(axis=0)

In [197]:
# label예측한 글 개수 = 원래 글 개수

len(pred_labels)

23481

In [199]:
# 원래데이터의 keywords'값만 뽑아서 'target'에 저장

target = list(data_sorted["keyword"])
print(target)

['개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발', '개발

In [200]:
# 'target'값(문자열)을 순서대로 '0 ~ 21'와 같은 숫자형으로 변환
# 즉, num_target이 실제 정답 list 이다.

num_target = []

for i in target:
    temp = i.replace('개발','0').replace('공예','1').replace('글쓰기','2').replace('금융','3').replace('데이터','4').replace('드로잉','5').replace('디자인','6').replace('베이킹','7').replace('부업','8').replace('사진','9').replace('성공 마인드','10').replace('아동 교육','11').replace('언어','12').replace('영상','13').replace('외국어','14').replace('요리','15').replace('운동','16').replace('음료','17').replace('음악','18').replace('재테크','19').replace('직무교육','20').replace('창업','21')
    num_target.append(int(temp))
    
print(num_target)

[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 

In [201]:
# 글숫자 맞음
len(num_target)

23481

In [202]:
from sklearn.metrics import confusion_matrix

#가로: 예측 클러스터 / 세로: 실제 클래스
pd.DataFrame(confusion_matrix(num_target, pred_labels))

0    1    2    3    4    5    6    7    8    9   ...   12   13   14   15  \
0    33  178    5    2   36   13    2   34    1  807  ...   29    2   13   27   
1    15  480    6    0    5   31   13    4   17   31  ...   32    5    6    0   
2    27  185    6    2   22   24   21   10    2  101  ...  121    5    6    1   
3    42   83    5    4   26   29    9  124    2  216  ...   28    4    8    5   
4    66  155    1    0   48   31   25   25    7  234  ...   37    6    6   12   
5   558  459    2    0    3   19   10    1    0    7  ...   15    1    0    0   
6   165  496    6    4   16   43   44   17    8  272  ...   34    4   22    0   
7    13  130    5    2    6   50   16    5   33   22  ...   14    5    6    1   
8    87  292    3  612   23   15   15   88    0  132  ...   35    1   20    4   
9   139   97   17    3   18   12  486   11   19   67  ...   44    9   12    6   
10    0   53    5    1    4    1    1   41    0   30  ...   29    0    3    0   
11    1   33    2    0    2    0    1    2    0   25  ...    4    3    0    0   
12   66  270    2    0   76   32    8   14   17  107  ...   55   10    7  463   
13  108  110   24    3   23   33   30   22   17   88  ...   69   25   17    3   
14   29   56    1    2  866    7    1    3    1   83  ...   25    0    7   18   
15   72  237   10    2   12   73   31   17  840   50  ...   33    1   14    0   
16   52  156  872    1   12   41   34    3   14   48  ...   31    2    7    1   
17   95  120   15    5   21   75   10    2   14   76  ...   27    2   19    4   
18  104  159   14    3   22  118   14    5    5   53  ...   49  589    9    1   
19   23  108    0    7   66   56    2  699    1   78  ...   34    5    8    1   
20    4   17    0    0    5    1    0    1    0  269  ...    6    0    2    0   
21   39  376    3    6   15   12    6   38    8  193  ...   63    4  566    2   

     16   17   18   19   20   21  
0     1    5    8    6   14    6  
1     0    8    3    5   12    6  
2     0    0   13    6    8    2  
3   499    1    7    4   24    2  
4     8    1    6   19   19   12  
5     0    2    0    5    0   16  
6     3   21    3   38   17  455  
7     0  561    2    6   24    2  
8     7    4    4   26   10    9  
9     3    8    5   33   39    6  
10    4    0    2    1    0    0  
11    1    0    8    4    0    0  
12    3    4  158   17   19    3  
13    2    5   19  402   38    5  
14    3    1  151    7    3    0  
15    0   38    9   12   51    3  
16    1    8    5    4   75    0  
17    1   26    7    8  613    3  
18    1    5   12   29   37    4  
19    9    2    3    4    6    1  
20    1    0    6    0    1    1  
21    7   11    5    5   19    6  

[22 rows x 22 columns]

In [203]:
cmatrix = confusion_matrix(num_target, pred_labels)

In [205]:
# best_label로 매칭했을 때 전체 클러스터링 정확도 계산 위해서 

best_labels = list(cmatrix.argmax(axis=0))

[5, 6, 16, 8, 14, 18, 9, 19, 15, 0, 4, 5, 2, 18, 21, 12, 3, 7, 12, 13, 17, 6]


In [212]:
#전체 클러스터링 정확도 계산 과정(성능확인)

i = 0
sum_result = 0
for c in cmatrix.transpose():
    i += 1
    sum_result += c[best_labels[i]]

IndexError: list index out of range

In [216]:
# 맞은 비율

sum_result/len(num_target)

0.10071973084621609

# 신규 데이터로 Test

In [59]:
#오늘일기에 작성된 글(전처리 과정 거침)을 list로 불러옴

from csv import reader

with open('testdata_list.csv', 'r', encoding='UTF-8') as csv_file:
    csv_reader = reader(csv_file)
    # Passing the cav_reader object to list() to get a list of lists
    list_of_rows = list(csv_reader)
    print(list_of_rows)

[['일과', '새벽', '식사', '준비', '등원', '등교', '준비', '집', '아침', '디즈니', '스타워즈', '청소', '설거지', '점심', '후다닥', '케이크', '사고', '책', '반납', '및', '대여', '애', '다시', '저녁', '식사', '후', '설거지', '정리', '방학', '기념', '케이크', '오늘', '방학', '날', '월', '일', '어', '두운', '날', '두', '아이', '벌써', '뭘', '하나', '걱정', '마음', '오늘', '아이', '위해', '동선', '상의', '케이크', '가게', '검색', '후', '출발', '너도밤나무', '제과점', '이름', '곳', '종류', '처음', '케이크', '가게', '홀', '케이크', '손', '점원', '무엇', '영어', '말', '제일', '인기', '건', '사진', '앞쪽', '거기', '초코', '코팅', '고심', '끝', '그', '두', '가지', '독일', '통방', '치즈', '케이크', '를', '역시', '종이', '포장', '환경', '진심', '사람', '년', '전통', '곳', '내', '고민', '공', '내', '봉투', '뭐', '독일인', '할아버지', '대체', '뭘', '한국', '문화원', '기존', '대여', '도서', '반납', '책', '한국', '책갈피', '트리', '장식', '혼자', '전시', '눈길', '둘', '틈', '대중', '교통', '어제', '오늘', '조금', '눈', '지하철', '선택', '알', '아들', '수', '안내', '방송', '출발', '간다', '하교', '시간', '늦', '것', '연락', '남편', '답', '주변', '람', '영어', '못', '지하철', '독일', '생활', '최초', '택시', '로', '무사', '도착', '방학', '기념', '케이크', '시식', '나이테', '켜', '바움쿠헨', '맛', '밀도', '식감', '도', '

In [60]:
#전처리 완료된 test글을 문장화

test_data = ' '.join(list_of_rows[0])

In [62]:
#해당 글을 nmf모델에 적용

new = [test_data]
label = nmf.transform(vec.transform(new)).argsort(axis=1)[:,-1][0]
label

17

In [63]:
# 모델에 따라서 묶여진 클러스터에 부여한 topic 이름을 가져옴
# test_data로 넣어준'오늘일기'와 비슷한 클러스터에 부여된 topic 이름을 출력함

pred_topic = topic_df['Label'][label]
pred_topic

'베이킹'

# 클래스101 강의 가져오기

In [64]:
### 참고사이트: https://coding-kindergarten.tistory.com/91

#step1.selenium 패키지와 time 모듈 import
from selenium import webdriver
from selenium.webdriver.common.keys import Keys
import time
from numpy import random

## 강의 추천 시스템 함수

In [71]:
def class_recommend(query):
    #크롬드라이버로 url로 접속
    url = 'https://class101.net/categories/'
    driver = webdriver.Chrome('/Users/parkjuhyeon/chromedriver')  ##크롬드라이버가 설치된 위치
    driver.get(url)
    time.sleep(3)
    
    #검색창에 키워드 입력 후 엔터
    search_box = driver.find_element_by_css_selector(".SearchInput__Input-go705p-2.bxkgtv")
    search_box.send_keys(query)
    search_box.send_keys(Keys.RETURN)
    time.sleep(2)
    
    
    # 결과 화면에서 강의명과 url 추출
    titles = driver.find_elements_by_css_selector(".Card__Title-sc-1esp5o0-4.bVCpyh")
    hrefs = driver.find_elements_by_css_selector(".ProductCardfragment__HoverStyledLink-sc-1cja13i-0.bzmYOj")
    titles_list =[]
    hrefs_list =[]
    for i in titles:
        title = i.text
        titles_list.append(title)
    
        for a in hrefs:
            href = a.get_attribute('href')
            if (href not in hrefs_list) :
                hrefs_list.append(href)

    ### 강의명, 링크 데이터프레임으로 만들기            
    data = {"class_title" : titles_list, "link" : hrefs_list}
    df = pd.DataFrame(data)
    
    return df

In [73]:
## 입력받은 pred_topic(예측한 라벨)에 대한 강의를 랜덤으로 3개 가져옴
class_recommend(pred_topic).sample(n=3)

<ipython-input-71-50a3da2bb3ed>:4: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome('/Users/parkjuhyeon/chromedriver')  ##크롬드라이버가 설치된 위치
<ipython-input-71-50a3da2bb3ed>:9: DeprecationWarning: find_element_by_* commands are deprecated. Please use find_element() instead
  search_box = driver.find_element_by_css_selector(".SearchInput__Input-go705p-2.bxkgtv")
<ipython-input-71-50a3da2bb3ed>:16: DeprecationWarning: find_elements_by_* commands are deprecated. Please use find_elements() instead
  titles = driver.find_elements_by_css_selector(".Card__Title-sc-1esp5o0-4.bVCpyh")
<ipython-input-71-50a3da2bb3ed>:17: DeprecationWarning: find_elements_by_* commands are deprecated. Please use find_elements() instead
  hrefs = driver.find_elements_by_css_selector(".ProductCardfragment__HoverStyledLink-sc-1cja13i-0.bzmYOj")


class_title  \
17  [🎁연말특가] 베이킹 초보자를 위한 레트로 빈티지 케이크 <동화 속 한순간을 담은 ...   
4          [🎁연말특가] 르꼬르동블루 출신 쉐프와 함께, 손쉬운 24가지 베이킹 레시피   
18      [🎁연말특가] 디저트에 디자인 그 이상을 담다, Our hours의 베이킹 클래스   

                                                 link  
17  https://class101.net/products/MCi1mG27vQLehmVZ...  
4   https://class101.net/products/YDkWioHDqYomCHn6...  
18  https://class101.net/products/JK8i78qMbIXi2ls9...